In [1]:
import os
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import pandas as pd


import numpy as np
from torch.utils.data import TensorDataset, DataLoader, RandomSampler
from gensim.models.keyedvectors import KeyedVectors
from sklearn.metrics.pairwise import cosine_similarity
from sacrebleu.metrics import BLEU
from tqdm import tqdm
from rouge_score import rouge_scorer
import seaborn as sns
import matplotlib.pyplot as plt



In [2]:
def load_vec(emb_path, nmax=50000):
    vectors = []
    word2id = {}
    with open(emb_path, 'r', encoding='utf-8', newline='\n', errors='ignore') as f:
        next(f)
        for i, line in enumerate(f):
            word, vect = line.rstrip().split(' ', 1)
            vect = np.fromstring(vect, sep=' ')
            assert word not in word2id, 'word found twice: {}'.format(word)
            vectors.append(vect)
            word2id[word] = len(word2id)
            if len(word2id) == nmax:
                break
    id2word = {v: k for k, v in word2id.items()}
    embeddings = np.vstack(vectors)
    word2emb = {}
    for word in word2id.keys():
        word2emb[word] = embeddings[word2id[word]]
    return word2emb

In [3]:
SOS_token = 0
EOS_token = 1

class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {}# {0: "SOS", 1: "EOS"}
        self.word2emb = {}
        if name == "eng":
            self.word2emb = load_vec("en.vec")
        if name == "spa":
            self.word2emb = load_vec("es.vec")
        self.n_words = 0  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

In [4]:
# Turn a Unicode string to plain ASCII, thanks to
# https://stackoverflow.com/a/518232/2809427
def unicodeToAscii(s):
    return ''.join(
        c for c in unicodedata.normalize('NFD', s)
        if unicodedata.category(c) != 'Mn'
    )

# Lowercase, trim, and remove non-letter characters
def normalizeString(s):
    s = unicodeToAscii(s.lower().strip())
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z!?]+", r" ", s)
    return s.strip()

In [5]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open('data/%s-%s.txt' % (lang1, lang2), encoding='utf-8').\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    lines = ['\t'.join(line.split('\t')[:2]) for line in lines]
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]
    random.shuffle(pairs)

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

In [6]:
MAX_LENGTH = 10

eng_prefixes = (
    "i am ", "i m ",
    "he is", "he s ",
    "she is", "she s ",
    "you are", "you re ",
    "we are", "we re ",
    "they are", "they re "
)

def filterPair(p):
    return len(p[0].split(' ')) < MAX_LENGTH and \
        len(p[1].split(' ')) < MAX_LENGTH and \
        p[1].startswith(eng_prefixes)


def filterPairs(pairs):
    return [pair for pair in pairs if filterPair(pair)]

In [7]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs

input_lang, output_lang, pairs = prepareData('eng', 'spa', True)
pairs_test = []
df_test = pd.read_excel("test.xlsx")
for pair in pairs:
    if pair[0] in list(df_test["Spanish"]):
        pairs_test.append([pair[0], pair[1]])
print(random.choice(pairs))

Reading lines...
Read 141370 sentence pairs
Trimmed to 9293 sentence pairs
Counting words...
Counted words:
spa 4397
eng 2994
['yo estoy cansada', 'i m tired']


In [8]:
complete_data = []
combined_index2word = {}
count = 0
for key in input_lang.index2word.keys():
    try:
        complete_data.append(input_lang.word2emb[input_lang.index2word[key]])
        combined_index2word[count] = input_lang.index2word[key]
        count += 1
    except Exception as e:
        pass
print("Total Spanish Words:", count)
spanish_count = count
for key in output_lang.index2word.keys():
    try:
        complete_data.append(output_lang.word2emb[output_lang.index2word[key]])
        combined_index2word[count] = output_lang.index2word[key]
        count += 1
    except Exception as e:
        pass
    
complete_data = np.array(complete_data)


Total Spanish Words: 3006


In [9]:
U, Sigma, Vt = np.linalg.svd(complete_data, full_matrices=False)
reduced_complete_data = np.dot(U[:, :128],np.diag(Sigma[:128]))


In [10]:
reduced_complete_data.shape

(5828, 128)

In [11]:
combined_word2emb_es = {}
combined_word2emb_en = {}
for i, v in enumerate(reduced_complete_data):
    if i < spanish_count:
        combined_word2emb_es[combined_index2word[i]] = reduced_complete_data[i].reshape((1,128))
    else:
        combined_word2emb_en[combined_index2word[i]] = reduced_complete_data[i].reshape((1,128))

In [12]:
input_sents = []
target_sents = []
pred_sents = []
for pair in tqdm(pairs_test):
    try:
        spanish_words = pair[0].split(' ')
        pred_words = []
        for word in spanish_words:
            max_sim = -1
            ans = ''
            for key in combined_word2emb_en.keys():
                sim = cosine_similarity(combined_word2emb_es[word], combined_word2emb_en[key])[0][0]
                if sim > max_sim:
                    max_sim = sim
                    ans = key
            pred_words.append(ans)
        prediction = ' '.join(pred_words)
        print("input:", pair[0], "\npred:", prediction, "\ntarget:", pair[1])
        input_sents.append(pair[0])
        target_sents.append(pair[1])
        pred_sents.append(prediction)
    except Exception as e:
        pass

  0%|          | 1/2783 [00:03<2:41:36,  3.49s/it]

input: estamos al corriente de eso 
pred: we the pressure of anyway 
target: we re aware of that


  0%|          | 2/2783 [00:09<3:38:04,  4.71s/it]

input: ella es dos anos mas joven que el 
pred: she is two years more young that the 
target: she s two years younger than him


  0%|          | 3/2783 [00:13<3:26:42,  4.46s/it]

...

input: voy a salir del pais 
pred: you to leave the presidential 
target: i m going to leave the country


100%|█████████▉| 2782/2783 [2:51:36<00:03,  3.39s/it]

input: no soy tan mayor 
pred: not me quite of 
target: i m not so old


100%|██████████| 2783/2783 [2:51:40<00:00,  3.70s/it]

input: el esta cruzando la calle ahora 
pred: the which crossing the street now 
target: he is crossing the street now


In [13]:
bleu = BLEU()
result = bleu.corpus_score(target_sents, [pred_sents])
print(result)

BLEU = 12.86 48.0/21.3/8.4/3.2 (BP = 1.000 ratio = 1.133 hyp_len = 16557 ref_len = 14608)


In [14]:
total_r1 = 0
total_r2 = 0
total_rl = 0
scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)

for pred, target in zip(pred_sents, target_sents):
    scores = scorer.score(pred, target)
    total_r1 += scores['rouge1'].fmeasure
    total_r2 += scores['rouge2'].fmeasure
    total_rl += scores['rougeL'].fmeasure
    
print("ROGUE-1", 100*total_r1/len(pred_sents))
print("ROGUE-2", 100*total_r2/len(pred_sents))
print("ROGUE-L", 100*total_rl/len(pred_sents))


ROGUE-1 51.12090012387994
ROGUE-2 22.336752459821053
ROGUE-L 48.273829621771505


In [15]:
words_vis = ["siempre", "always", "muy", "very", "ella", "she", "conocida", "known", "casado", "married", "interesante", "interesting", "con", "with", "ahora", "now", "dos", "two", "anos", "years", "hablando", "talking"]
combined_word2emb = {}
combined_word2emb.update(combined_word2emb_es)
combined_word2emb.update(combined_word2emb_en)
combined_word2emb_vis = {}
for w in words_vis:
    combined_word2emb_vis[w] = combined_word2emb[w].reshape((128,))

In [16]:
words, vectors = zip(*combined_word2emb_vis.items())

# Calculate cosine similarity between word vectors
similarity_matrix = cosine_similarity(vectors)

# Create a heatmap using seaborn
sns.set(font_scale=8)
plt.figure(figsize=(150, 120))
sns.heatmap(similarity_matrix, annot=True, xticklabels=words, yticklabels=words, cmap="YlGnBu")

# Add labels and title
plt.xlabel('Words')
plt.ylabel('Words')
plt.title('Cosine Similarity Heatmap of Word Vectors')

# Show the plot
plt.show()